ZZ Left Off Here:

-Finish Embedding Matrix

-Set up HAN layers

# <font color='purple'>Predicting Song Genres Using Lyrical Analysis</font>

<i>Authors</i>: Zachary Zalman, Jacob Mannix

<i>Date</i>: 16 May 2020

### Load In Needed Materials and Functions

In [1]:
import pandas as pd
from datetime import datetime
from tqdm import tqdm_notebook as tqdm
import ast
import re

import numpy as np

import spacy

import gensim
from gensim.models import Doc2Vec
from gensim.models.doc2vec import TaggedDocument

from sklearn import utils
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split

from nltk.tokenize.treebank import TreebankWordDetokenizer

import tensorflow as tf
from tensorflow import keras

spacy.prefer_gpu()

unable to import 'smart_open.gcs', disabling that module


False

In [2]:
# define a function to turn the string of lyric tokens into a list of lyric tokens
def format_column(text):

    lyrics_list = ast.literal_eval(text)
    
    result = []
    
    # loop through every lyric to remove the newline character
    for entry in lyrics_list:

        if entry != '\n ':
            result.append(entry)
        else:
            continue
    
    return result

### First Time Creation of Tokens

In [ ]:
# load in the lyrics data set
first_df = pd.read_csv("lyrics.csv")

In [ ]:
# create a song id number by renaming the index
first_df.rename(columns={"index":"song_id"}, inplace=True)
first_df.shape

In [ ]:
first_df.dropna(subset=['lyrics'], inplace=True)
first_df.shape

In [ ]:
# split the dataframe
info = first_df[["song_id", "song", "year", "artist", "genre"]]
lyrics = first_df[["song_id", "lyrics"]]

print(info.columns)
print(lyrics.columns)

In [ ]:
# load the spaCy object with the english corpus
nlp = spacy.load("en_core_web_md")

Creating a tokenizer pipeline

In [ ]:
# define the lemmatizer function
def lemmatizer(doc):
    # remove the PRON (which are pronouns after lemming)
    doc = [token.lemma_ for token in doc if token.lemma_ != '-PRON-']
    doc = u' '.join(doc)
    return nlp.make_doc(doc)

def remove_punct(doc):
    # remove punctuation -> Use token.text to return strings, needed for Gensim.
    doc = [token.text for token in doc if token.is_punct != True]
    return doc


# add_pipe adds the function to the tokenizer
nlp.add_pipe(lemmatizer,name='lemmatizer',after='ner')
nlp.add_pipe(remove_punct, name="punct", last=True)

In [ ]:
# get the column of lyrics
doc = lyrics.lyrics
doc

In [ ]:
# check to see if any lyrics are missing
doc.isna().sum()

In [ ]:
# laptop time to run = 
# desktop time to run = 

doc_list = []

# go through each song
for doc in tqdm(doc):
    
    # tokenize the document
    pr = nlp(doc)
    
    # add it to the list
    doc_list.append(pr)

In [ ]:
# check a list of tokens
doc_list[0]

In [ ]:
# turn the list into a series, then turn it into a dataframe
temp = pd.DataFrame(pd.Series(doc_list), columns=["tokens"])

# reset the indices of the original df and the token df
temp.reset_index(drop=True, inplace=True)
first_df.reset_index(drop=True, inplace=True)

# merge the tokens df onto the original df using the indicies
df_with_tokens = pd.merge(first_df, temp, left_index=True, right_index=True)

Save and load the data as needed

In [ ]:
# save the df
df_with_tokens.to_csv("lyrics_with_tokens.txt", sep="|", index=False)

In [3]:
# load in the dat set if it has already been created
df = pd.read_csv("lyrics_with_tokens.txt", sep="|")

In [4]:
df = df[df.genre != "Not Available"]
df = df[df.genre != "Other"]
df.genre.value_counts()
df

song_id                         song  year           artist    genre  \
0             0                    ego-remix  2009  beyonce-knowles      Pop   
1             1                 then-tell-me  2009  beyonce-knowles      Pop   
2             2                      honesty  2009  beyonce-knowles      Pop   
3             3              you-are-my-rock  2009  beyonce-knowles      Pop   
4             4                black-culture  2009  beyonce-knowles      Pop   
...         ...                          ...   ...              ...      ...   
266552   362232    who-am-i-drinking-tonight  2012       edens-edge  Country   
266553   362233                         liar  2012       edens-edge  Country   
266554   362234                  last-supper  2012       edens-edge  Country   
266555   362235  christ-alone-live-in-studio  2012       edens-edge  Country   
266556   362236                         amen  2012       edens-edge  Country   

                                                   lyrics  \
0       Oh baby, how you doing?\nYou know I'm gonna cu...   
1       playin' everything so easy,\nit's like you see...   
2       If you search\nFor tenderness\nIt isn't hard t...   
3       Oh oh oh I, oh oh oh I\n[Verse 1:]\nIf I wrote...   
4       Party the people, the people the party it's po...   
...                                                   ...   
266552  I gotta say\nBoy, after only just a couple of ...   
266553  I helped you find her diamond ring\nYou made m...   
266554  Look at the couple in the corner booth\nLooks ...   
266555  When I fly off this mortal earth\nAnd I'm meas...   
266556  I heard from a friend of a friend of a friend ...   

                                                   tokens  
0       ['oh', 'baby', 'how', 'do', '\n ', 'know', 'be...  
1       ['playin', 'everything', 'so', 'easy', '\n ', ...  
2       ['if', 'search', '\n ', 'for', 'tenderness', '...  
3       ['oh', 'oh', 'oh', 'oh', 'oh', 'oh', '\n ', 'v...  
4       ['party', 'the', 'people', 'the', 'people', 't...  
...                                                   ...  
266552  ['got', 'to', 'say', '\n ', 'boy', 'after', 'o...  
266553  ['help', 'find', 'diamond', 'ring', '\n ', 'ma...  
266554  ['look', 'at', 'the', 'couple', 'in', 'the', '...  
266555  ['when', 'fly', 'off', 'this', 'mortal', 'eart...  
266556  ['hear', 'from', 'a', 'friend', 'of', 'a', 'fr...  

[237427 rows x 7 columns]

### Use Doc2Vec For Embeddings

In [ ]:
# shuffle the df before splitting
df = shuffle(df)
df.reset_index(inplace=True, drop=True)
df

In [ ]:
# perform a test/train split on the data
train, test = train_test_split(df, test_size=0.3, random_state=42)

In [ ]:
# turn the training data into tagged documents
# train_tagged = train.apply(lambda r: TaggedDocument(words=format_column(r['tokens']), tags=[r.genre]), axis=1)
# train_tagged

train_tagged = [TaggedDocument(words=format_column(_d.lower()), tags=[str(i)]) for i, _d in enumerate(train.tokens)]
train_tagged

In [ ]:
# turn the test data into tagged documents
# test_tagged = test.apply(lambda r: TaggedDocument(words=format_column(r['tokens']), tags=[r.genre]), axis=1)
# test_tagged

test_tagged = [TaggedDocument(words=format_column(_d.lower()), tags=[str(i)]) for i, _d in enumerate(test.tokens)]
test_tagged

In [ ]:
train_tagged[0]

Creating the model

In [ ]:
# create the parameters of the Doc2Vec model
model = Doc2Vec(vector_size=300,
                window=5, 
                alpha=.025, 
                min_alpha=0.00025, 
                min_count=2, 
                dm=1, 
                workers=8)

# build the vocab of the model
model.build_vocab(train_tagged)

In [ ]:
# define the epochs count
epochs = range(50)

# loop through each epoch
for epoch in epochs:
    
    print(f'Epoch {epoch+1}')
    
    # train the model on the training data
    model.train(train_tagged,
                total_examples=model.corpus_count,
                epochs=model.epochs)
    
    # decrease the learning rate
    model.alpha -= 0.00025
    
    # fix the learning rate, no decay
    model.min_alpha = model.alpha
     
model.save('lyricsDoc2Vec.model')

In [ ]:
# load in the model if its already trained
# model = Doc2Vec.load('lyricsDoc2Vec.model')

Creation of test/train X and y arrays

In [ ]:
X_train = np.array([model.docvecs[str(i)] for i in range(len(train_tagged))])
y_train = train['genre']

In [ ]:
X_test = np.array([model.infer_vector(test_tagged[i][0]) for i in range(len(test_tagged))])
y_test = test['genre']

In [ ]:
X_train[0]

## Networks With Doc2Vec

### Regular CNN

### Regular RNN

### RNN-CNN

## Networks With Internal Embeddings

### Regular CNN

### Regular RNN

### RNN-CNN

# Hierarchical Attention Network

Define the lyrics and genre lists

In [5]:
# get the tokens of the lyrics, and turn it into a list
lyrics_list = df['tokens']
lyrics_list = lyrics_list.to_list()

lyr_list = []

# loop through all of the songs, and get a list of the tokens from each string
for lyr in lyrics_list:
    temp = ast.literal_eval(lyr)
    lyr_list.append(temp)
    
len(lyr_list)

237427

In [6]:
# get the genres and turn it into a list
genre_list = df['genre']
gen_list = genre_list.to_list()

len(gen_list)

237427

### Setting Up The Embeddings

Word2Vec

In [7]:
# turn the lyrics into a list of sentences (assuming each line is the equivilent of a sentence)

# create a blank list
result = []

# loop through every lyric
for i in lyr_list:
    tmp = []
    
    # if the entry is a newline indicator, remove it and start a new list tmp
    for entry in i:
        if entry != '\n ':
            tmp.append(entry)
        else:
            result.append(tmp)
            tmp = []
    result.append(tmp)

result

[['oh', 'baby', 'how', 'do'],
 ['know', 'be', 'go', 'to', 'cut', 'right', 'to', 'the', 'chase'],
 ['some', 'woman', 'be', 'make', 'but'],
 ['like',
  'to',
  'think',
  'that',
  'be',
  'create',
  'for',
  'a',
  'special',
  'purpose'],
 ['know', 'what', 'be', 'more', 'special', 'than', 'feel'],
 ['be', 'on', 'baby', 'let', 'get', 'lose'],
 ['do',
  'not',
  'need',
  'to',
  'call',
  'into',
  'work',
  'because',
  'be',
  'the',
  'boss'],
 ['for', 'real', 'want', 'to', 'show', 'how', 'feel'],
 ['consider', 'lucky', 'that', 'be', 'a', 'big', 'deal'],
 ['why', 'well', 'get', 'the', 'key', 'to', 'heart'],
 ['but',
  'be',
  'not',
  'go',
  'to',
  'need',
  'would',
  'rather',
  'open',
  'up',
  'body'],
 ['and', 'show', 'secret', 'do', 'not', 'know', 'be', 'inside'],
 ['no', 'need', 'for', 'to', 'lie'],
 ['be', 'too', 'big', 'be', 'too', 'wide'],
 ['be', 'too', 'strong', 'will', 'not', 'fit'],
 ['be', 'too', 'much', 'be', 'too', 'tough'],
 ['talk', 'like', 'this', 'because', '

In [8]:
result2 = []

# loop through every line, pulling the index and the actual list
for index, value in enumerate(result):

    # lowercase everyhing and turn into a string
    temp_lower = [x.lower() for x in value]
    temp = " ".join(temp_lower)
    
    # skip the line if it is a verse indicator
    if re.search(r"verse [1-9]", temp):
        continue
        
    # remove any song markers from the data (these are single item lists with values that indicate song parts)
    if temp != 'chorus' and temp != 'intro' and temp != 'outro hook' and temp != 'bridge' and temp != 'pre hook' and temp != 'hook':
        result2.append(temp_lower)

In [134]:
result2[0]

['hear',
 'from',
 'a',
 'friend',
 'of',
 'a',
 'friend',
 'of',
 'a',
 'friend',
 'that',
 '.']

In [10]:
# create the word2vec model based on the lyrics corpus
w2v_model = gensim.models.Word2Vec(result2, min_count=5, workers=4, size=100)

In [11]:
# test a value to see the vector
w2v_model['hello']

C:\Users\blitz\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  


array([-0.62186015, -0.03081499, -0.21088746, -0.9404178 ,  1.5323417 ,
        1.1026163 , -0.6581831 , -1.197121  ,  0.76107925, -0.27720302,
        0.74015915,  0.8530537 , -0.75827366,  0.57737654,  2.3484998 ,
        2.2322319 ,  1.0569925 ,  1.4794186 ,  1.3531991 ,  0.45144802,
        0.7864085 ,  0.08894753,  0.01034185,  0.75298434,  0.2806667 ,
        0.02656571,  0.12500265,  0.04055892, -2.3798375 ,  1.6818494 ,
        1.1694028 ,  0.30173498,  2.0692148 ,  0.7521247 ,  0.41060916,
       -2.7583375 ,  1.1821675 ,  0.61659974,  1.1926575 ,  0.06369991,
       -1.0429554 ,  0.9131621 ,  0.92173505, -1.4665481 , -1.0739368 ,
       -1.3736498 ,  0.28156996,  0.36892614,  1.1523886 , -0.5871328 ,
       -0.20985293, -1.4102672 ,  1.3724604 , -0.7669808 , -0.2322595 ,
       -0.291449  , -0.18782498,  0.7566911 , -0.13958815,  0.613164  ,
        1.2961273 ,  1.0722051 , -0.96042424,  0.72260976, -1.1011611 ,
        0.32878098, -2.115819  ,  1.1682072 ,  1.6013042 ,  0.21

In [12]:
# number of words in the vocab
vocab_len = len(w2v_model.wv.vocab)
vocab_len

95224

Make an embedding matrix

In [32]:
words_dict = {}

# loop through all the words in the vocab and associate it with it's vector in a dictionary
for key in w2v_model.wv.vocab:
    vector = w2v_model[key]
    word = key
    words_dict[word] = vector

C:\Users\blitz\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  """


In [38]:
for i, word in words_dict.items():
    print(i)

oh
baby
how
do
know
be
go
to
cut
right
the
chase
some
woman
make
but
like
think
that
create
for
a
special
purpose
what
more
than
feel
on
let
get
lose
not
need
call
into
work
because
boss
real
want
show
consider
lucky
big
deal
why
well
key
heart
would
rather
open
up
body
and
secret
inside
no
lie
too
wide
strong
will
fit
much
tough
talk
this
can
back
ego
such
huge
love
walk
usually
humble
now
choose
leave
with
or
could
have
blue
arrogant
confident
decide
when
find
damn
kill
leg
yet
thigh
matter
fact
smile
maybe
eye
boy
site
see
kind
of
something
so
must
admit
every
reason
bitch
if
beat
sing
piano
playin
everything
easy
seem
sure
still
way
then
thing
come
along
though
truly
ask
as
linger
delight
bring
just
try
really
say
even
through
dark
day
may
strange
about
word
slip
out
feeling
i
from
bear
all
time
hold
in
courage
speak
listen
tell
there
wrong
fasten
sound
melody
alright
sleep
same
exactly
hear
new
act
mind
stay
by
search
tenderness
hard
live
look
truthfulness
blind
always
give
honest

era
amores
matan
dao
aquella
infeliz
alguien
conoce
tanto
al
llorar
eres
hablar
terminamos
este
cuento
acabado
tale
guy
zeke
battle
creek
pepsi
hole
sensation
yell
lust
anyhow
tender
swell
sir
onto
cheer
ba
soo
pleasure
kindness
jesus
repay
andre
3000
regret
dick
wet
old
dry
tread
troubled
odd
stack
hook-
hundred
puff
pipe
tiny
penny
wall
lost
my
conversation
breakup
wherever
worried
1
drake
wassup
bedtime
kingdom
married
carry
beyoncã
fuck
8
late
ghost
i'mma
thriller
talking
five
ten
swear
funny
ex
running
nigga
palm
two
different
mirror
view
forward
frank
ocean
subtle
shark
scared
spare
law
sky
plenty
oohhh
x3
presenter
winner
knowles
female
vocalist
clapping
judge
parent
houston
drift
knowledge
cat
solemn
solomon
flight
midnight
beach
forest
preach
gutter
ignore
climb
shit
bore
label
planet
working
9
5
ah
rou
und
probably
reap
sow
perfection
haunt
lull
sheet
wicked
tongue
runway
slap
pin
doorway
bite
challenger
group
nina
nicky
kelly
ashley
hip
hop
rappin
girls
tyme
h
drippin
candy


automobile
pus
aah
joint
dedicate
alia
tame
brag
nut
dine
artist
public
announcement
smoker
blunt
inhale
exhale
sell
dank
bahamas
cutlass
tree
simon
hog
fingernail
steadily
hungry
fiendin
cabbage
habit
llac
hottie
blowin
shotgun
lac
holiday
inn
choppin
spaghetti
voodoo
3x
chokin
dicke
hint
hennesey
buddha
naw
dunno
maker
faker
formula
mega
ignorant
gay
dapper
slurp
careful
bein
torchin
oughta
tryina
amg
refer
snitch
conviction
fakin
foo
charm
homies
muthafuckin
manipulator
category
trustin
hooker
mandatory
suckin
everybodie
'cause
faze
tracy
nuffin
brew
digi
quik
babyface
broke
lucrative
panty
nite
tramp
slut
riff
raff
crab
scratchin
bleedin
disgusting
mah
definetly
cindy
fatal
robin
dana
novita
marcy
karen
april
str8
muthaphukkaz
layin
muthaphuka
yellin
saggin
bailin
ren
muthaphukka
exact
tombstone
map
yella
galore
tighter
glove
playaz
getz
studio
script
salt
notion
fillmoe
h.p.
dwell
army
wiggle
mink
rug
remote
forte
airplane
hesitation
golden
4-tay
glock
pursuin
treacherous
smooth
d

uptown
disc
jockey
rotation
chart
fm
percussion
easin
producer
combine
airplay
rhymin
subject
comprehend
tnt
plop
cuty
naz
ahaha
territory
whatta
limpin
nitty
gritty
impersonate
romey
platform
wonderin
ballpark
franks
plump
aaaaah
weird
makeup
adsbygoogle
=
window.adsbygoogle
||
.push
chris
noone
uuuuu
cherished
deeper
oooooo
oah
sail
rebuilt
choru


mend
anchor
shooting
shadows
stormy
time'll
slander
stagnate
classmate
graduate
restraint
neighbor
prejudice
bigot
pair
lense
impaired
vision
chrous
powder
normal
topic
goner
audition
accidentally
grave
accord
turnin
inferno
affirmative
impermanent
visit
limited
lend
pedestrian
stray
handed
fraction
vanish
advantage
glorious
priority
abuse
fairy
conceal
fraud
coffin
behave
brace
shaken
identity
crisis
license
vice
denim
opponent
message
breathin
force
martial
pierce
metaphorical
dart
verbal
noose
assault
diagnose
overload
victory
chord
metaphor
mightier
sword
almighty
endure
wayward
compact
analysis
ancient
masse
enthusiastic
opposite
poet

echt
timeline
meinst
schaden
selbst
gestorben
einer
jordan
neues
sã¼ãe
pics
schwestern
and'rer
meinung
paperboy
erreichen
ziele
einmal
kã¶nn'n
genie
steckt
setzen
energie
frei
geb
zweifeln
richten
liga
starten
dollars
entfliehen
moloch
tower
bau
ihn
hã¶her
kilometer
zahl
schwarzen
stadt
jagen
darin
baden
gewinnen
mei'm
ã¶ffne
flieg
gedacht
appetit
fliegt
harten
zeiten
zeigen
schneller
jamaica
bauen
herrschen
warlord
bergauf
wille
mã¼ssen
entscheiden
verkauf
hemd
karten
konzert
woll'n
gefedert
geteert
vermisst
lange
beginnen
atmet
musik
ritalin
dk
melodien
fangen
erziehen
benutzen
autotune
lieben
konsum
exzess
dom
pã
rignon
buddel
peng
turbo
hã¤ngst
deiner
hã¤ngen
sven
kinderzimmer
neulich
oval
chili
mosh
fã¼hlst
soundtrack
krach
danach
gitarren
fall'n
rahman
lalalala
bumm
null
noten
meile
hast
midlife
seele
braucht
feiert
afflict
lycanthropy
wolf
takeover
charles
manson
sod
heretic
awaited
return
grudge
drunken
berkely
university
herpe
fetid
virgin
raper
bend
steamy
rape
mob
toilet
cu

...

abreuve
sillons
l'immense
câur
cã´te
zigue
mã´m
mãªm
d'printemps
t'y
dehor
d'paumã
hiboux
sortons
chichis
d'l'autr
connaissais
remplis
terr
bals
lisas
vultures
iiit
muhaha
steada
j.a
wantta
preguntã¡ndole
chingar
completita
babbette
meate
dimpled
lubbin
hw
rock-'n'-roll
breakin'outta
vuleka
thunderhead
correlation
imaginarium
aiden
l&n
yeuh
t.o.r.n.a.d.o
insegna
fidi
risorgeremo
perdonerã²
vedrã²
beoneul
gieogeun
b.i.n.g.o
umklammert
schicksals
sprn
whywhy
flitter
yaye
gaiji
i?)(can
chicalinda
sance
818
cuzz
downset
patriarchal
macklemore
puhun
mustaa
enemp
lihan
dwellers
telocvovim
kelley
razum
trekkin
klingons
vizuliza
navagatin
freres
routes
mnent
tempte
auprs
avide
continuent
sabertooth
toese
moering
londoner
samaa
matkaa
tehtiin
vapaa
matka
helpompaa
palamaan
vaihdan
suuntaa
kiitos
ainakaan
kiveen
kysyt
ede
haluan
pysty
laskeutuu
selitt
tahtoisitko
tapahtuu
parempaa
tyyppi
kvi
seaward
time.without
----------chorus
varien
squinty
leveau
f2d
diaboli
frosset
svunnet
kjã
morket
horde

marnay
d'voir
l'cou
l'train
adle
conducteur
l'nord
leclerc
jtais
quelquun
confier
l'toile
choisira
peins
aimera
mlanie
d'abraham
l'attente
cachs
harpe
allais
parc'que
delirant
volcanos
t'oublierai
l'amitie
l'accident
palier
lanie
l'ocan
m'aide
plaignez
changeait
d'amiti
mettrai
m'aimera
cognait
appã
d'asile
ntait
jjg
plamondon
trahit
foncent
l'amitiã
auteur
courais
carosse
flish
trang
apperance
demie
quichotte
virevolte
goã»ts
disparais
d'humains
solitudes
d'eternite
manteaux
chanterait
loue
t'est
serrent
cocotiers
chameaux
serts
caravanes
rivages
lagons
l'escampette
bruule
finiront
tournera
raisonnent
tamtam
chantes
dvorant
premiã¨res
bagne
t'arrive
codes
j'pourrais
la.i.la.i.la.i.la.i.la.i.la.i.la
semer
habite
volez
s'apprend
religieuse
bluh
adormeces
crecã­a
l'oxygne
j'allume
conduira
naziland
accro
l'oxygã¨ne
retrouverai
melangent
romã
ãcris
redonne
bercera
qu'ensemble
virtuel
passerais
armure
ãcrire
idees
entãªtant
sã¨ve
choisit
meep
phantastic
luxuriant
thrillful
bonebag
kasota

gã¶zlérimdé
télaå
ã¼midimé
yoldaå
birgé
gélméyésén
uäur
gétir
ã¶yréåib
tutarä±m
gã¶zã¼mde
yaåä±mä±
ãlã¼m
istérém
olmasa
kã¶ã§
géldin
olmuåam
sevmérém
qalan
yaå
yaåayamam
didem
nerelere
gidem
mesut
kurdun
dã¼nyamä±
yä±kä±pta
yä±llar
dã¶zénlérindir
ã¶tdã¼
dilé
qapä±nä±
gã¶rérsén
uã§urumlar
baälamaz
gã¶nlã¼m
sevemezse
gã¼nã¼mde
yarä±nä±mda
gecdi
namiq
qaraã§uxurlu
oluram
dã¼z
elémirém
baälanä±ram
hélé
tezdir
aldadä±ram
denén
ã¼zã¼m
qä±zlar
hã¶rã¼kléri
léã§éyidir
bakä±nä±n
gã¶zlã¼
qä±zlarä±
gã¼lér
ã¼zlã¼
bakä±
dinmé
odlanä±r
xézér
sã¶nmé
kã¼smé
payä±zä±n
eåqindén
dã¶nmé
béxtimdén
hézin
allaha
marå
dã¶nméz
dã¶nér
daim
bayraää±
iã§di
lham
qélbimdésén
åérab
sã¼z
badé
déymésin
ã§ä±xsana
sã¼zséné
sés
baxä±ålar
istér
dã¼zdã¼mã¼
ã¼zdã¼mã¼
baäã§anä±n
qã¶nã§ésin
gecikdim
gã¼nã¼ndé
aälamaya
alä±åtä±rdä±n
qayä±tmä±r
yaåananlar
birimizi
sevék
bizdén
danä±åsä±n
deyék
gã¼lék
kã¼sméyék
ésméyék
alä±åsä±n
istéyir
ã§ä±xä±

soad
sharmana
parda
yall(dollar
duhdee
adnde
vaoo
ncredible
awaaaaaaaaaaaaay
duta
jeni
arike
j'rã
enrã
lossa
d'euros
keblo
tatouã
boloss
myah
tchoins
enculã
l'cul
l'empãªche
ponge
rappes
l'infrã
quentable
infrã
scalpled
ð´ð²ð¸ð³ð
ñðµð»ñ
championless
dietin
colson
bumpty
ooom
xcx
chinaon
chowa
mannaneunji
junghwa
solji
boryeogo
hyerin
ë¹ê¸
gamgoseo
svalkar
vã¤rmer
sã¤ker
lã¤ngtar
rã¤dda
trumma
allte
vã¤xer
nightwatchman
diggady
a.f.d.
fruitkwan
fairytalz
frukwan
mindstates
potium
everlastic
librase
ahnd
wup
witten
kikoeteru
tocha
cyjan
hurtado
paaarrrrk
kalage
haterville
km.g
koss
tchou
f#7
d9
bboys
bgirls
yauch
flange
3-pack
m.c.a
kuniff
beasie
ubdia
tippi
illingest
ryall
-does
altamira
skarecrows
diiiee
abunaikara
yoberu
justice-
4q
macosa
oh(yea
faggoty
beddy
keed
cranbrook
grayed
minithin
shoobeedoo
pway
murdaaaaa
3pac
sqwad
kaniff
suc
motherf***ing
damn)(ooh
shit)(oh
faack
shadys
doodi
ohhhohhh
ronhe
boosh
ca$his
dr.dre
gord
menal
i'be
faceplant
nonnie
cowbobobobobobo
ooklah
ch

infanta
shankill
butchers
springville
faerghail
4thof
bios
gã¸re
elongate
wahnsinnige
zeittotschlger
geschlossene
verstrker
idon
zumbate
muerdeme
pillarla
charlatanes
alisten
fecas
tiiiiiiiiiiiii
recompenza
adopte
wiso
mistika
linguistica
veridica
envalen
tikiri
rrra
pistoleo
fulete
bichifucker
explotã³
averã­a
colorao
wippy
fumal
bailandote
experimenten
tmida
combinan
fornaris
demustrame
chiquititos
movio
confiesale
cuidaras
juane
donqueo
sillita
hebilla
campeando
nada(que
popola
say'dem
k47
chokechain
menyanyi
hipnotizas
insospechado
antonini
amparar
ravenwreck
kokka
oblate
yona
sunadokei
kowasenai
aza
konbeki
koukatsu
jintai
harisakete
kururi
furari
kurari
muguchina
fesutibaru
drole
montaigu
merai
sabrer
capsuler
prets
colorã
l'adrã
spaaaaace
waldura
kailer
irido
hyorin
isaram
isarang
hyosung
cantarã
sereis
brilleaux
wilko
scuffling
psychomania
foresaken
discoman
gã¼nun
birinde
opinionized
victimised
socialised
molestados
sardos
greã±udos
topos
haganse
satanismo
pw
huevones
hierbita

In [ ]:
embedding_matrix = np.zeros((vocab_len, 100))

for word in list(words_dict.keys()):
    embedding_matrix[i] = words_dict.get(word)

print('Total absent words are', absent_words, 'which is', "%0.2f" % (absent_words * 100 / len(word_index)),
      '% of total words')
print('Words with '+str(min_wordCount)+' or less mentions', small_words, 'which is', "%0.2f" % (small_words * 100 / len(word_index)),
      '% of total words')
print(str(len(word_index)-small_words-absent_words) + ' words to proceed.')

### Setting Up The Model

Preprocessing the lyrics

In [129]:
result3 = []

# loop through all the songs in the dataset
for song in tqdm(lyr_list):
    
    result = []
    result2 = []
    tmp = []
    
    # loop through all the lines in a song
    for word in song:
    
        # if the token is a newline, replace it with a period. otherwise append the token to the list
        if word != '\n ':
            tmp.append(word)
        else:
            tmp.append('.')
            result.append(tmp)
            tmp = []
        
    # loop through all the lines again
    for index, value in enumerate(result):

        # lowercase everyhing and turn into a string
        temp_lower = [x.lower() for x in value]
        temp = " ".join(temp_lower)
        
        # skip the line if it is a verse indicator
        if re.search(r"verse [1-9]", temp):
            continue
            
        # remove any song markers from the data (these are single item lists with values that indicate song parts)
        if temp != 'chorus' and temp != 'intro' and temp != 'outro hook' and temp != 'bridge' and temp != 'pre hook' and temp != 'hook':
            result2.append(temp_lower)
    
    # append the processed song to the list
    result3.append(result2)

C:\Users\blitz\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  after removing the cwd from sys.path.


In [130]:
result3[0]

[[['oh', 'baby', 'how', 'do', '.'],
  ['know', 'be', 'go', 'to', 'cut', 'right', 'to', 'the', 'chase', '.'],
  ['some', 'woman', 'be', 'make', 'but', '.'],
  ['like',
   'to',
   'think',
   'that',
   'be',
   'create',
   'for',
   'a',
   'special',
   'purpose',
   '.'],
  ['know', 'what', 'be', 'more', 'special', 'than', 'feel', '.'],
  ['be', 'on', 'baby', 'let', 'get', 'lose', '.'],
  ['do',
   'not',
   'need',
   'to',
   'call',
   'into',
   'work',
   'because',
   'be',
   'the',
   'boss',
   '.'],
  ['for', 'real', 'want', 'to', 'show', 'how', 'feel', '.'],
  ['consider', 'lucky', 'that', 'be', 'a', 'big', 'deal', '.'],
  ['why', 'well', 'get', 'the', 'key', 'to', 'heart', '.'],
  ['but',
   'be',
   'not',
   'go',
   'to',
   'need',
   'would',
   'rather',
   'open',
   'up',
   'body',
   '.'],
  ['and', 'show', 'secret', 'do', 'not', 'know', 'be', 'inside', '.'],
  ['no', 'need', 'for', 'to', 'lie', '.'],
  ['be', 'too', 'big', 'be', 'too', 'wide', '.'],
  ['be', '

In [137]:
lyr_list_final = []

# loop through all the songs
for song in tqdm(result3):
    
    lyr_list_str = []
    
    # loop through each line in the song, and merge all the tokens together
    for i in range(len(song)):
        temp = TreebankWordDetokenizer().detokenize(song[i])
        lyr_list_str.append(temp)
    
    # turn the list of strings into one string
    lyr_list_str = ", ".join(lyr_list_str)
    
    # replace the list element separator with a period to show line end
    lyr_list_str = lyr_list_str.replace('.,', '.')
    
    # append the lyrics string to the list
    lyr_list_final.append(lyr_list_str)

C:\Users\blitz\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  after removing the cwd from sys.path.


In [141]:
lyr_list_final[7765]

"should not be hard to find. will be the one with big mouth move. big word say nothing. hope know. be not father's fault be such a bore. and so afraid of everything. be keep inside live in mind. hope that the telephone do not ring. with be all right pain be universal baby. and worry about what be go to sing. be stay in and save up energy. know day be come. and when find will rewind. and play over again a hundred time. and when hear will not fear. will say back again and say be fine. relief relief."

Setting up the layers of the model

In [ ]:
#####################################################################################################################
# define the attention layer (from https://humboldt-wi.github.io/blog/research/information_systems_1819/group5_han/)
#####################################################################################################################
"""
    Hierarchial Attention Layer as described by Hierarchical Attention Networks for Document Classification(2016)
    - Yang et. al.
    Source: https://www.cs.cmu.edu/~hovy/papers/16HLT-hierarchical-attention-networks.pdf
    Theano backend
"""

class AttentionLayer(keras.layers.Layer):

    def __init__(self,attention_dim=100,return_coefficients=False,**kwargs):
        # Initializer 
        self.supports_masking = True
        self.return_coefficients = return_coefficients
        self.init = initializers.get('glorot_uniform') # initializes values with uniform distribution
        self.attention_dim = attention_dim
        super(AttentionLayer, self).__init__(**kwargs)

    def build(self, input_shape):
        # Builds all weights
        # W = Weight matrix, b = bias vector, u = context vector
        assert len(input_shape) == 3
        self.W = K.variable(self.init((input_shape[-1], self.attention_dim)),name='W')
        self.b = K.variable(self.init((self.attention_dim, )),name='b')
        self.u = K.variable(self.init((self.attention_dim, 1)),name='u')
        self.trainable_weights = [self.W, self.b, self.u]

        super(AttentionLayer, self).build(input_shape)

    def compute_mask(self, input, input_mask=None):
        return None

    def call(self, hit, mask=None):
        # Here, the actual calculation is done
        uit = K.bias_add(K.dot(hit, self.W),self.b)
        uit = K.tanh(uit)
        
        ait = K.dot(uit, self.u)
        ait = K.squeeze(ait, -1)
        ait = K.exp(ait)
        
        if mask is not None:
            ait *= K.cast(mask, K.floatx())

        ait /= K.cast(K.sum(ait, axis=1, keepdims=True) + K.epsilon(), K.floatx())
        ait = K.expand_dims(ait)
        weighted_input = hit * ait
        
        if self.return_coefficients:
            return [K.sum(weighted_input, axis=1), ait]
        else:
            return K.sum(weighted_input, axis=1)

    def compute_output_shape(self, input_shape):
        if self.return_coefficients:
            return [(input_shape[0], input_shape[-1]), (input_shape[0], input_shape[-1], 1)]
        else:
            return input_shape[0], input_shape[-1]

In [ ]:
##################################################################################################################
# define the model layers (from https://humboldt-wi.github.io/blog/research/information_systems_1819/group5_han/)
##################################################################################################################

# Parameters
MAX_SENTENCE_NUM = 30
MAX_WORD_NUM = 40
MAX_FEATURES = vocab_len

# Words level attention model
word_input = Input(shape=(MAX_WORD_NUM,), dtype='int32',name='word_input')
word_sequences = embedding_layer(word_input)
word_gru = Bidirectional(GRU(50, return_sequences=True),name='word_gru')(word_sequences)
word_dense = Dense(100, activation='relu', name='word_dense')(word_gru) 
word_att,word_coeffs = AttentionLayer(EMBED_SIZE,True,name='word_attention')(word_dense)
wordEncoder = Model(inputs = word_input,outputs = word_att)

# Sentence level attention model
sent_input = Input(shape=(MAX_SENTENCE_NUM,MAX_WORD_NUM), dtype='int32',name='sent_input')
sent_encoder = TimeDistributed(wordEncoder,name='sent_linking')(sent_input)
sent_gru = Bidirectional(GRU(50, return_sequences=True),name='sent_gru')(sent_encoder)
sent_dense = Dense(100, activation='relu', name='sent_dense')(sent_gru) 
sent_att,sent_coeffs = AttentionLayer(EMBED_SIZE,return_coefficients=True,name='sent_attention')(sent_dense)
sent_drop = Dropout(0.5,name='sent_dropout')(sent_att)
preds = Dense(5, activation='softmax',name='output')(sent_drop)

In [ ]:
# compile model
model = Model(sent_input, preds)
model.compile(loss='categorical_crossentropy',optimizer='adam',metrics=['acc'])
print(wordEncoder.summary())
print(model.summary())

In [ ]:
# train the model
history = model.fit(x_train, y_train, validation_data=(x_val, y_val), epochs=7, batch_size=32)